# **Group Assignment** - Bike Sharing

- `instant`: record index
- `dteday` : date
- `season` : season (1:springer, 2:summer, 3:fall, 4:winter)
- `yr` : year (0: 2011, 1:2012)
- `mnth` : month ( 1 to 12)
- `hr` : hour (0 to 23)
- `holiday` : weather day is holiday or not (extracted from http://dchr.dc.gov/page/holiday-schedule)
- `weekday` : day of the week
- `workingday` : if day is neither weekend nor holiday is 1, otherwise is 0.
+ `weathersit` : 
	- 1: Clear, Few clouds, Partly cloudy, Partly cloudy
	- 2: Mist + Cloudy, Mist + Broken clouds, Mist + Few clouds, Mist
	- 3: Light Snow, Light Rain + Thunderstorm + Scattered clouds, Light Rain + Scattered clouds
	- 4: Heavy Rain + Ice Pallets + Thunderstorm + Mist, Snow + Fog
- `temp` : Normalized temperature in Celsius. The values are divided to 41 (max)
- `atemp`: Normalized feeling temperature in Celsius. The values are divided to 50 (max)
- `hum`: Normalized humidity. The values are divided to 100 (max)
- `windspeed`: Normalized wind speed. The values are divided to 67 (max)
- `casual`: count of casual users
- `registered`: count of registered users
- `cnt`: count of total rental bikes including both casual and registered

# Import Libraries

In [1]:
import pandas as pd
import plotly.express as px

from sklearn.model_selection import train_test_split
from xgboost import XGBRegressor
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint, uniform
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler

import pickle


# Load Data

In [2]:
data = pd.read_csv('data/bike-sharing_hourly.csv')

In [3]:
data.head()

instant      dteday  season  yr  mnth  hr  holiday  weekday  workingday  \
0        1  2011-01-01       1   0     1   0        0        6           0   
1        2  2011-01-01       1   0     1   1        0        6           0   
2        3  2011-01-01       1   0     1   2        0        6           0   
3        4  2011-01-01       1   0     1   3        0        6           0   
4        5  2011-01-01       1   0     1   4        0        6           0   

   weathersit  temp   atemp   hum  windspeed  casual  registered  cnt  
0           1  0.24  0.2879  0.81        0.0       3          13   16  
1           1  0.22  0.2727  0.80        0.0       8          32   40  
2           1  0.22  0.2727  0.80        0.0       5          27   32  
3           1  0.24  0.2879  0.75        0.0       3          10   13  
4           1  0.24  0.2879  0.75        0.0       0           1    1

# PART I: Exploratory Data Analysis

## Data Quality

### Basic statistics, unique values, nulls, and duplicates

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17379 entries, 0 to 17378
Data columns (total 17 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   instant     17379 non-null  int64  
 1   dteday      17379 non-null  object 
 2   season      17379 non-null  int64  
 3   yr          17379 non-null  int64  
 4   mnth        17379 non-null  int64  
 5   hr          17379 non-null  int64  
 6   holiday     17379 non-null  int64  
 7   weekday     17379 non-null  int64  
 8   workingday  17379 non-null  int64  
 9   weathersit  17379 non-null  int64  
 10  temp        17379 non-null  float64
 11  atemp       17379 non-null  float64
 12  hum         17379 non-null  float64
 13  windspeed   17379 non-null  float64
 14  casual      17379 non-null  int64  
 15  registered  17379 non-null  int64  
 16  cnt         17379 non-null  int64  
dtypes: float64(4), int64(12), object(1)
memory usage: 2.3+ MB


In [5]:
data.describe()

instant        season            yr          mnth            hr  \
count  17379.0000  17379.000000  17379.000000  17379.000000  17379.000000   
mean    8690.0000      2.501640      0.502561      6.537775     11.546752   
std     5017.0295      1.106918      0.500008      3.438776      6.914405   
min        1.0000      1.000000      0.000000      1.000000      0.000000   
25%     4345.5000      2.000000      0.000000      4.000000      6.000000   
50%     8690.0000      3.000000      1.000000      7.000000     12.000000   
75%    13034.5000      3.000000      1.000000     10.000000     18.000000   
max    17379.0000      4.000000      1.000000     12.000000     23.000000   

            holiday       weekday    workingday    weathersit          temp  \
count  17379.000000  17379.000000  17379.000000  17379.000000  17379.000000   
mean       0.028770      3.003683      0.682721      1.425283      0.496987   
std        0.167165      2.005771      0.465431      0.639357      0.192556   
min        0.000000      0.000000      0.000000      1.000000      0.020000   
25%        0.000000      1.000000      0.000000      1.000000      0.340000   
50%        0.000000      3.000000      1.000000      1.000000      0.500000   
75%        0.000000      5.000000      1.000000      2.000000      0.660000   
max        1.000000      6.000000      1.000000      4.000000      1.000000   

              atemp           hum     windspeed        casual    registered  \
count  17379.000000  17379.000000  17379.000000  17379.000000  17379.000000   
mean       0.475775      0.627229      0.190098     35.676218    153.786869   
std        0.171850      0.192930      0.122340     49.305030    151.357286   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.333300      0.480000      0.104500      4.000000     34.000000   
50%        0.484800      0.630000      0.194000     17.000000    115.000000   
75%        0.621200      0.780000      0.253700     48.000000    220.000000   
max        1.000000      1.000000      0.850700    367.000000    886.000000   

                cnt  
count  17379.000000  
mean     189.463088  
std      181.387599  
min        1.000000  
25%       40.000000  
50%      142.000000  
75%      281.000000  
max      977.000000

In [6]:
data.nunique()

instant       17379
dteday          731
season            4
yr                2
mnth             12
hr               24
holiday           2
weekday           7
workingday        2
weathersit        4
temp             50
atemp            65
hum              89
windspeed        30
casual          322
registered      776
cnt             869
dtype: int64

In [7]:
for column in data.columns:
    col_name = (column + ": ").ljust(20, " ")
    print(col_name, *data[column].unique()[0:5], sep="\t", end="\n")

instant:            	1	2	3	4	5
dteday:             	2011-01-01	2011-01-02	2011-01-03	2011-01-04	2011-01-05
season:             	1	2	3	4
yr:                 	0	1
mnth:               	1	2	3	4	5
hr:                 	0	1	2	3	4
holiday:            	0	1
weekday:            	6	0	1	2	3
workingday:         	0	1
weathersit:         	1	2	3	4
temp:               	0.24	0.22	0.2	0.32	0.38
atemp:              	0.2879	0.2727	0.2576	0.3485	0.3939
hum:                	0.81	0.8	0.75	0.86	0.76
windspeed:          	0.0	0.0896	0.2537	0.2836	0.2985
casual:             	3	8	5	0	2
registered:         	13	32	27	10	1
cnt:                	16	40	32	13	1


In [8]:
data.isnull().sum()

instant       0
dteday        0
season        0
yr            0
mnth          0
hr            0
holiday       0
weekday       0
workingday    0
weathersit    0
temp          0
atemp         0
hum           0
windspeed     0
casual        0
registered    0
cnt           0
dtype: int64

In [9]:
duplicates = data[data.duplicated()]
print(f"Number of duplicates found: {len(duplicates)}")

Number of duplicates found: 0


### Data Types

It doesnt look like we need to encode the categorical variables. They are for the most part ordinal. Like `weathersit` which goes from light weather to heavy weather.

In [10]:
data['dteday'] = pd.to_datetime(data['dteday'])
data['dateHour'] = data['dteday'] + pd.to_timedelta(data['hr'], unit='h')

In [11]:
numerical_features = ['temp', 'atemp', 'hum', 'windspeed']
category_features = ['season', 'yr', 'mnth', 'hr', 'holiday', 'weekday', 'workingday', 'weathersit']

## Data Visualization

First lets look at the count data behavior for both years

In [12]:
daily_counts = data.groupby(['dteday'])['cnt'].sum().reset_index()
monthly_y1_df = daily_counts[daily_counts['dteday'].dt.year == 2011].reset_index(drop=True)
monthly_y2_df = daily_counts[daily_counts['dteday'].dt.year == 2012].reset_index(drop=True)
monthly_y2_df['2011'] = monthly_y1_df['cnt']
monthly_y2_df['2012'] = monthly_y2_df['cnt']
compare_graph = px.line(monthly_y2_df, x='dteday', y=['2012', '2011'],
            labels={'cnt': 'Total Bike Counts', 'dteday': 'Date', 'year': 'Year'},
            template='ggplot2')
compare_graph.update_layout(title='2011 vs 2012 Bike Usage Comparison')
compare_graph.show()

We can look at individual months, but there is no trend around specific days of the month so it why it almost looks like white noise. What you can see is that some months clearly have a higher demand than others, which can lead us to plan strategies around specific months of the year.

In [13]:
# Average bike count by day for each month of the year
monthly_counts = data.copy()
monthly_counts['month'] = monthly_counts['dateHour'].dt.month
monthly_counts['day'] = monthly_counts['dateHour'].dt.day
monthly_counts['year'] = monthly_counts['dateHour'].dt.year

# Dictionary to map month number to name
month_names = {1: 'January', 2: 'February', 3: 'March', 4: 'April', 5: 'May', 6: 'June',
               7: 'July', 8: 'August', 9: 'September', 10: 'October', 11: 'November', 12: 'December'}

# Calculate the average count of bikes for each day of the week, hour, and month
avg_counts = monthly_counts.groupby(['month', 'day'])['cnt'].mean().reset_index()

# Replace numeric weekday and month values with corresponding names
avg_counts['month'] = avg_counts['month'].map(month_names)

# Plotly Express line chart
fig = px.line(avg_counts, x='day', y='cnt', color='month',
              labels={'cnt': 'Average Bike Counts', 'hr': 'Hour of the Day', 'weekday': 'Day of the Week', 'month': 'Month'},
              title='Average bike count by day for each month of the year')

# Show the Plotly chart
fig.show()

We can see the behavior of bike counts between different days of the week. You can tell that weekend days behave very different from week days, probably because of commute hours.

In [14]:
# Dictionary to map weekday number to name
weekday_names = {0: 'Sunday', 1: 'Monday', 2: 'Tuesday', 3: 'Wednesday', 4: 'Thursday', 5: 'Friday', 6: 'Saturday'}

# Calculate the average count of bikes for each day of the week and hour
avg_counts = data.groupby(['weekday', 'hr'])['cnt'].mean().reset_index()

# Replace numeric weekday values with corresponding names
avg_counts['weekday'] = avg_counts['weekday'].map(weekday_names)

# Plotly Express line chart
fig = px.line(avg_counts, x='hr', y='cnt', color='weekday',
              labels={'cnt': 'Average Bike Counts', 'hr': 'Hour of the Day', 'weekday': 'Day of the Week'},
              title='Average Bike Counts by Hour for Each Day of the Week')

# Show the Plotly chart
fig.show()

We can check that the day with most rentals was September 15th.

In [32]:
# Group data by day and sum the number of rentals
daily_rentals = data.groupby('dteday')['cnt'].sum()

# Get the date with the highest number of rentals
max_rentals = daily_rentals.idxmax()
max_rentals_count = daily_rentals.max()
print(f"The day with the most rentals was {max_rentals} with {max_rentals_count} rentals")

The day with the most rentals was 2012-09-15 00:00:00 with 8714 rentals


Lets look at the correlation between our numerical values. There are strong correlations within our variables, which makes sense given that they are all related to temperature.

In [16]:
# Calculate correlation matrix
correlation_matrix = data[numerical_features].corr()

# Create a Plotly Express heatmap for the correlation matrix
fig = px.imshow(correlation_matrix,
                labels=dict(color="Correlation"),
                x=correlation_matrix.columns,
                y=correlation_matrix.columns,
                title="Correlation Matrix Heatmap",
                template='ggplot2')

# Show the Plotly chart
fig.show()

We can see the behavior of bike rentals is affected by the temperature.

In [17]:
# temperature vs rentals
fig = px.scatter(data, x='temp', y='cnt', trendline='ols')
fig.show()

Looking at the box plots for the numerical values, we can see that there are various outliers for the feature `windspeed` which we can deal with later. There is a `0` in `hum` which could represent a missing value.

In [18]:
# Create a Plotly Express box plot
fig = px.box(data[numerical_features],
             title='Box Plot for Numerical Features',
             labels={'variable': 'Feature', 'value': 'Value'})

# Customize x-axis labels rotation
fig.update_layout(xaxis=dict(tickangle=90))

# Show the Plotly chart
fig.show()

## Feature Engineering

Let's create a copy of the data that we can engineer.

In [19]:
prepared_df = data.copy()

### Feature Selection

We will remove values that are not relevant for training the model.

In [20]:
columns_to_drop = ['instant', 'dteday', 'casual', 'registered', 'yr', 'dateHour']
prepared_df = prepared_df.drop(columns=columns_to_drop)

### Missing Values and Outliers

Since we found outliers in `windspeed`, and a 0 (missing value) in `hum`, we will replace them with upper or lower limits of the IQR.

In [21]:
def impute_outliers(df, column):
    # Calculate the first quartile (Q1) and third quartile (Q3)
    Q1 = df[column].quantile(0.25)
    Q3 = df[column].quantile(0.75)

    # Calculate the interquartile range (IQR)
    IQR = Q3 - Q1

    # Define the lower and upper limits
    lower_limit = Q1 - 1.5 * IQR
    upper_limit = Q3 + 1.5 * IQR

    # Replace outliers with the lower and upper limits
    df[column] = df[column].apply(lambda x: upper_limit if x > upper_limit else lower_limit if x < lower_limit else x)

impute_outliers(prepared_df, 'windspeed')
impute_outliers(prepared_df, 'hum')



Now if we lok at the box plot again, we will see no outliers in our data.

In [22]:
# Create a Plotly Express box plot
fig = px.box(prepared_df[numerical_features],
             title='Box Plot for Numerical Features',
             labels={'variable': 'Feature', 'value': 'Value'})

# Customize x-axis labels rotation
fig.update_layout(xaxis=dict(tickangle=90))

# Show the Plotly chart
fig.show()

# PART II: Prediction Model

## Arrange the data

In [23]:
X = prepared_df.drop(['cnt'], axis=1)
y = prepared_df['cnt']

In [24]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

## Create a pipeline

For our model, a pipeline was created that would scale all the values and use a Gradient Descent algorithm, in this case XGBoost, for training and predictions.We started using a Linear Regression, that is why we included a scaler in the pipeline. Unfortunately, the size of the pickled model was higher that what is allowed by GitHub. We need the files up in GitHub for deployment, so we went with XGBoost instead because of its lighter file size.

In [25]:
xgb = XGBRegressor(objective='reg:squarederror', random_state=0)

param_grid = {"max_depth": randint(3, 10),
             'min_child_weight': randint(1, 5),
             "learning_rate": uniform(0.03, 0.3),
             "n_estimators": randint(100, 150),
             "colsample_bytree": uniform(0.7, 0.3),
             "gamma": uniform(0, 0.5),
             "subsample": uniform(0.6, 0.4)
             }

In [26]:
# Define the preprocessor to drop columns and apply standard scaling
preprocessor = ColumnTransformer(
    transformers=[
        ('Sacler', StandardScaler(), X.columns)
    ]
)

pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('regressor', xgb)  # Replace with your chosen regression model
])

xgb_cv = RandomizedSearchCV(pipeline, param_grid, scoring='neg_mean_squared_error', cv=5, refit='neg_mean_squared_error', n_jobs=-1, verbose=2, n_iter=20, return_train_score=True)

## Fit the model

In [27]:
# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Evaluate the model on the test set
score = pipeline.score(X_train, y_train)
print(f'Model Score: {score}')

Model Score: 0.9362438047268302


## Evaluate

In [28]:
# Test the model
y_pred = pipeline.predict(X_test)

# Clip the predictions so that there are no negative values
y_pred = y_pred.clip(min=0)
pd.Series(y_pred)

0       468.077881
1        55.007660
2         5.090073
3       508.708405
4        28.170235
           ...    
3471     31.388670
3472     27.455696
3473    153.425674
3474    279.550812
3475    332.395233
Length: 3476, dtype: float32

In [29]:
# test scores
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

mse = mean_squared_error(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print(f'Mean Squared Error: {mse}')
print(f'Mean Absolute Error: {mae}')
print(f'R^2 Score: {r2}')

Mean Squared Error: 3836.798554837483
Mean Absolute Error: 41.60288619384667
R^2 Score: 0.8788331370759699


From our scores we can see that the train and test scores are not significantly different, which tells us that the model is not highly overfitted.

In [30]:
# scatter plot of the test target variable with plotly
fig = px.scatter(x=y_test, y=y_pred, labels={'x': 'True Values', 'y': 'Predicted Values'}, title='Predicted vs True Values')
fig.add_shape(type='line', line=dict(dash='dash'), x0=y_test.min(), x1=y_test.max(), y0=y_test.min(), y1=y_test.max())
fig.show()


## Save the model

In [31]:
# Pickle the model
with open('models/reg.pickle', 'wb') as to_write:
    pickle.dump(pipeline, to_write)

# PART III: Streamlit dashboard